<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Running-CNN-for-Interactive-Testing" data-toc-modified-id="Running-CNN-for-Interactive-Testing-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Running CNN for Interactive Testing</a></span></li><li><span><a href="#Random-seed-golden-list-stuff" data-toc-modified-id="Random-seed-golden-list-stuff-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Random seed golden list stuff</a></span></li></ul></div>

In [ ]:
%matplotlib inline
%load_ext autoreload
%autoreload 2

import os,sys
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from datetime import datetime

import SimpleITK as sitk
from scipy import ndimage as ndi
import skimage as skim
from skimage import feature
import pandas as pd
import xarray as xr
plt.rcParams['figure.figsize'] = (10,8)
import pickle as pkl
from tensorboardX import SummaryWriter
from torch.utils.data import Dataset, DataLoader
import torchvision.utils
from torchsummary import summary
import torch
import torch.nn as nn
from collections import defaultdict
import torch.nn.functional as F
import torch.optim as optim
from torch.optim import lr_scheduler
from torchvision import models
import time
import copy

%aimport mre 
from mre import pytorch_arch
%aimport mre.mre_datasets
from mre.mre_datasets import MRETorchDataset, MREtoXr, TorchToXr
%aimport mre.plotting
from mre.plotting import hv_dl_vis, hv_pred_comp, xr_viewer_v2
%aimport mre.train_mre_model
from mre.train_mre_model import train_model_full
%aimport mre.prediction
from mre.prediction import add_predictions, get_linear_fit

import holoviews as hv
from holoviews import opts
hv.extension('bokeh')




In [ ]:
# Load mre data
# xr_maker = MREtoXr(from_file='/pghbio/dbmi/batmanlab/Data/MRE/XR_full_gold_clinical_v3/*.nc')
# ds = xr_maker.get_ds()
#out_dir = '/pghbio/dbmi/batmanlab/bpollack/predictElasticity/data'

## Running CNN for Interactive Testing

In [ ]:
#data_path = '/pghbio/dbmi/batmanlab/Data/MRE/XR_trimmed_with_contrast_gold/'
# data_path = '/pghbio/dbmi/batmanlab/Data/MRE/XR_with_contrast_full_gold/'
# data_path = '/pghbio/dbmi/batmanlab/Data/MRE/XR_full_gold_v3/'
# data_path = '/pghbio/dbmi/batmanlab/Data/MRE/XR_full_gold_clinical_v3/'
data_path = '/ocean/projects/asc170022p/shared/Data/MRE/XR_full_gold_clinical_v3/'
#data_path = '/pghbio/dbmi/batmanlab/Data/MRE/XR_wave_gold_v1/'
data_file = '*.nc'
output_path = '/ocean/projects/asc170022p/bpollack/predictElasticity/data'
torch.cuda.empty_cache()
# now = '2020-02-20_12-04-13'
now = datetime.today().strftime('%Y-%m-%d_%H-%M-%S')
print(now)

kwargs = dict(seed=33, num_epochs=1, n_layers=5, channel_growth=True,
              model_cap=18, batch_size=4, num_workers=1,
              gamma=0.3, lr_scheduler='step', step_size=30, lr=1e-3,
              # lr_scheduler='cyclic', step_size=15, lr_max=0.001, lr_min=1e-5,
              #loss='ordinal', out_channels_final=108, bins='uniform',
              # loss='ordinal', out_channels_final=76, bins='blocks',
              wave=False,
              wave_hypers=[0.005, 0.01, 0.5, 0.1],
              fft=False,
              lap_kernel=3,
              class_only=True,
              in_channels=14, 
              # inputs=['t2', 't1_pre_water', 't1_pos_160_water', 't1_pre_fat'],
              inputs=['t2'],
              loss='l2',
              out_channels_final=5,
              model_arch='clinical',
              pixel_weight=0.5,
              sampling_breakdown='smart',
              dataset_ver='rad_freeze',
              do_clinical=True, norm_clinical=True, do_clinical_only=True,
              subj=['1045', '1329', '1714', '1935'],
              # subj=['0898', '0924', '1119', '1795', '1917', '2046'],
              #subj=['1106', '1853', '0173', '0737', '1426', '1712', '0995', '1464'],
              # subj=['1483', '1296', '1642', '1967', '0932', '1706', '0173', '0653'],
              # subj=['2046', '1819', '0509', '0734', '0659', '1400', '1578', '1893'],
              erode_mask=10,
              smear_amt=25,
              train_aug=True,
              train_smear='none',
              train_sample='shuffle',
              depth=True,
              dims=3, # 2D or 3D model arch
              # inputs=['t1_pre_water'],
              worker_init_fn = 'rand_epoch',
              test_aug=False,
              test_smear='none',
              val_aug=False,
              val_smear='none',
              val_sample='shuffle',
              do_val=True,
              transfer=False,
              norm='bn',
              dry_run=False)

train_model_output = train_model_full(data_path, data_file, output_path, model_version=f'notebook_test_{now}', **kwargs)


In [6]:
# ds_torch = TorchToXr(inputs, masks, targets, names).ds
ds_torch = TorchToXr(train_model_output[0], train_model_output[2], train_model_output[1], train_model_output[3], sequences=['t2', 't1_pre_water', 't1_pos_160_water', 't1_pre_fat']).ds
xr_viewer_v2(ds_torch, size=350, prediction=False, torch=True)

:Dataset   [subject,mask_type,y,z,x,sequence]   (image_mri,mask_mri)
:Dataset   [mre_type,subject,mask_type,y,z,x]   (image_mre,mask_mre)


/home/bpollack/conda_envs/mre/lib/python3.6/site-packages/holoviews/plotting/util.py:685: MatplotlibDeprecationWarning: The global colormaps dictionary is no longer considered public API.
  [cmap for cmap in cm.cmap_d if not
/home/bpollack/conda_envs/mre/lib/python3.6/site-packages/holoviews/plotting/util.py:685: MatplotlibDeprecationWarning: The global colormaps dictionary is no longer considered public API.
  [cmap for cmap in cm.cmap_d if not
/home/bpollack/conda_envs/mre/lib/python3.6/site-packages/holoviews/plotting/util.py:685: MatplotlibDeprecationWarning: The global colormaps dictionary is no longer considered public API.
  [cmap for cmap in cm.cmap_d if not
/home/bpollack/conda_envs/mre/lib/python3.6/site-packages/holoviews/plotting/util.py:685: MatplotlibDeprecationWarning: The global colormaps dictionary is no longer considered public API.
  [cmap for cmap in cm.cmap_d if not
/home/bpollack/conda_envs/mre/lib/python3.6/site-packages/holoviews/plotting/util.py:685: Matplotlib

/home/bpollack/conda_envs/mre/lib/python3.6/site-packages/holoviews/plotting/util.py:685: MatplotlibDeprecationWarning: The global colormaps dictionary is no longer considered public API.
  [cmap for cmap in cm.cmap_d if not
/home/bpollack/conda_envs/mre/lib/python3.6/site-packages/holoviews/plotting/util.py:685: MatplotlibDeprecationWarning: The global colormaps dictionary is no longer considered public API.
  [cmap for cmap in cm.cmap_d if not
/home/bpollack/conda_envs/mre/lib/python3.6/site-packages/holoviews/plotting/util.py:685: MatplotlibDeprecationWarning: The global colormaps dictionary is no longer considered public API.
  [cmap for cmap in cm.cmap_d if not
/home/bpollack/conda_envs/mre/lib/python3.6/site-packages/holoviews/plotting/util.py:685: MatplotlibDeprecationWarning: The global colormaps dictionary is no longer considered public API.
  [cmap for cmap in cm.cmap_d if not
/home/bpollack/conda_envs/mre/lib/python3.6/site-packages/holoviews/plotting/util.py:685: Matplotlib

Column
    [0] WidgetBox
        [0] Select(margin=(20, 20, 5, 20), name='subject', options=['0898', '0924', ...], value='0898', width=250)
        [1] Select(margin=(0, 20, 5, 20), name='mask_type', options=['combo'], value='combo', width=250)
        [2] DiscreteSlider(formatter='%d', margin=(5, 20, 20, 20), name='z', options=OrderedDict([('0', ...]), value=0, width=250)
        [3] FloatSlider(name='mask transparency', value=0.7)
        [4] RangeSlider(end=2, name='contrast', start=-2, step=1, value=(-1, 1))
        [5] RangeSlider(end=120, name='mre contrast', step=1, value=(0, 100))
        [6] RangeSlider(end=20, name='wave contrast', start=-20, step=1, value=(-10, 10))
    [1] HoloViews(Layout)

In [3]:
#from_file = '/pghbio/dbmi/batmanlab/Data/MRE/XR_with_contrast_full_gold/*.nc'
#from_file = '/pghbio/dbmi/batmanlab/Data/MRE/XR_full_gold_v3/*.nc'
from_file = '/pghbio/dbmi/batmanlab/Data/MRE/XR_wave_gold_v1/*.nc'
# now = '2019-12-13_12-05-05'
#now = '2019-12-19_20-52-42' #(standard 2D training)
# now = '2019-12-19_22-12-26' #(overfit 2D training)
#now = '2019-12-21_22-34-20'
#now = '2019-12-31_17-47-33'
#now = '2020-01-02_18-31-17'
# now = '2020-01-06_10-37-35'
#now = '2020-01-17_17-20-32'
# now = '2020-01-20_18-51-20'
#now = '2020-11-17_15-58-55' # First run for wave and stiff (no helmholtz)
# now = '2020-11-22_16-26-33' # eval for best starting omega_eff
now = '2020-11-23_11-36-51' # first attempt at helmholtz

# xr_maker = MREtoXr(
#     from_file=from_file,
#     from_file_pred=f'/pghbio/dbmi/batmanlab/bpollack/predictElasticity/data/XR/notebook_test_{now}/train/*.nc')
# ds_train = xr_maker.get_ds()
# ds_train = ds_train.load()
xr_maker = MREtoXr(
    from_file=from_file,
    # from_file_pred=f'/pghbio/dbmi/batmanlab/bpollack/predictElasticity/data/XR/notebook_test_{now}/test/*.nc')
    from_file_pred=f'/pghbio/dbmi/batmanlab/bpollack/predictElasticity/data/XR/{now}_n0/test/*.nc')
ds_test = xr_maker.get_ds()
ds_test = ds_test.load()
# xr_maker = MREtoXr(
#     from_file=from_file,
#     from_file_pred=f'/pghbio/dbmi/batmanlab/bpollack/predictElasticity/data/XR/notebook_test_{now}/val/*.nc')
# ds_val = xr_maker.get_ds()
# ds_val = ds_val.load()

Called by IPython.
Within IPython QtConsole.
pylab loaded, but not in inline mode.
['0898' '0924' '1119' '1795' '1917' '2046']
['0006' '0020' '0024' '0029' '0043' '0047' '0084' '0126' '0135' '0155'
 '0164' '0172' '0173' '0175' '0210' '0213' '0219' '0221' '0222' '0234'
 '0235' '0291' '0344' '0378' '0384' '0395' '0401' '0415' '0457' '0461'
 '0490' '0491' '0492' '0496' '0509' '0510' '0516' '0525' '0556' '0564'
 '0604' '0612' '0615' '0628' '0639' '0648' '0650' '0653' '0655' '0659'
 '0693' '0704' '0727' '0734' '0735' '0737' '0740' '0747' '0748' '0892'
 '0898' '0900' '0914' '0924' '0929' '0931' '0932' '0937' '0954' '0964'
 '0975' '0979' '0989' '0995' '1028' '1033' '1039' '1045' '1053' '1072'
 '1075' '1076' '1077' '1083' '1103' '1106' '1108' '1110' '1119' '1121'
 '1123' '1138' '1144' '1149' '1205' '1207' '1209' '1215' '1217' '1230'
 '1239' '1250' '1266' '1271' '1278' '1287' '1296' '1303' '1311' '1329'
 '1336' '1337' '1341' '1343' '1344' '1360' '1367' '1382' '1395' '1400'
 '1404' '1412' '1417'

In [ ]:
ds_test

In [5]:
xr_viewer_v2(ds_test, size=350, prediction=True)

NameError: name 'ds_test' is not defined

In [ ]:
np.percentile?

In [ ]:
skim.exposure.rescale_intensity?

In [ ]:
skim.exposure.equalize_adapthist?

In [ ]:
df_strat = pd.read_pickle('/pghbio/dbmi/batmanlab/bpollack/predictElasticity/data/MRE/df_strat_v0.pkl')

In [ ]:
df_strat.loc[ds_val.subject]['mre'].hist(bins=100)

In [ ]:
%%capture --no-display
xr_viewer_v2(ds_test, size=250, prediction=True)

In [ ]:
get_linear_fit(ds_test, do_cor=False)

## Random seed golden list stuff

In [ ]:
golden = ['0006', '0020', '0029', '0043', '0126', '0135', '0164', '0173', '0210', '0219', '0234',
       '0235', '0291', '0344', '0395', '0401', '0415', '0461', '0491', '0492', '0509', '0510',
       '0556', '0564', '0612', '0628', '0653', '0655', '0659', '0693', '0704', '0734', '0735',
       '0737', '0747', '0748', '0830', '0838', '0860', '0872', '0890', '0898', '0904', '0914',
       '0929', '0931', '0932', '0937', '0940', '0954', '0975', '0979', '0989', '0995', '1028',
       '1033', '1045', '1072', '1076', '1077', '1083', '1103', '1106', '1110', '1119', '1121',
       '1123', '1144', '1149', '1209', '1215', '1217', '1271', '1278', '1287', '1296', '1303',
       '1311', '1329', '1336', '1337', '1341', '1343', '1344', '1360', '1367', '1382', '1395',
       '1400', '1404', '1412', '1417', '1426', '1427', '1433', '1435', '1447', '1448', '1453',
       '1456', '1464', '1474', '1483', '1491', '1504', '1526', '1529', '1530', '1541', '1545',
       '1550', '1554', '1561', '1574', '1577', '1578', '1579', '1590', '1595', '1603', '1642',
       '1667', '1671', '1679', '1694', '1699', '1706', '1712', '1714', '1715', '1720', '1722',
       '1727', '1736', '1748', '1765', '1785', '1786', '1789', '1790', '1791', '1793', '1795',
       '1798', '1806', '1819', '1829', '1839', '1843', '1851', '1853', '1883', '1893', '1896',
       '1899', '1903', '1935', '1940', '1948', '1967', '1979', '1980', '2001', '2007', '2029',
       '2034', '2046']
np.random.seed(100)
np.random.shuffle(golden)
golden[0:8]

In [ ]:
[golden[i*8:i*8+8] for i in range(21)]